<a href="https://colab.research.google.com/github/weedge/doraemon-nb/blob/main/demo/VibeVoice_podcast.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# VibeVoice Colab — T4 Quickstart (1.5B)

This notebook provides a quickstart guide to run VibeVoice on Colab with T4. The T4 GPU can only support the 1.5B model due to memory limitations. Please note that T4 can only use SDPA instead of flash_attention_2, which may result in unstable and lower audio quality. For the best TTS experience, we recommend trying the 7B model on a more powerful GPU.

## Risks and Limitations

While efforts have been made to optimize it through various techniques, it may still produce outputs that are unexpected, biased, or inaccurate. VibeVoice inherits any biases, errors, or omissions produced by its base model (specifically, Qwen2.5 1.5b in this release). Potential for Deepfakes and Disinformation: High-quality synthetic speech can be misused to create convincing fake audio content for impersonation, fraud, or spreading disinformation. Users must ensure transcripts are reliable, check content accuracy, and avoid using generated content in misleading ways. Users are expected to use the generated content and to deploy the models in a lawful manner, in full compliance with all applicable laws and regulations in the relevant jurisdictions. It is best practice to disclose the use of AI when sharing AI-generated content.

## Step 1: Setup Environment

In [1]:
# Check for T4 GPU
import torch
if torch.cuda.is_available() and "T4" in torch.cuda.get_device_name(0):
    print("✅ T4 GPU detected")
else:
    print("""
    ⚠️ WARNING: T4 GPU not detected

    The recommended runtime for this Colab notebook is "T4 GPU".

    To change the runtime type:

        1. Click on "Runtime" in the top navigation menu
        2. Click on "Change runtime type"
        3. Select "T4 GPU"
        4. Click "OK" if a "Disconnect and delete runtime" window appears
        5. Click on "Save"

    """)

# Clone the VibeVoice repository
![ -d /content/VibeVoice ] || git clone --quiet --branch main --depth 1 https://github.com/microsoft/VibeVoice.git /content/VibeVoice
print("✅ Cloned VibeVoice repository")

# Install project dependencies
!uv pip --quiet install --system -e /content/VibeVoice
print("✅ Installed dependencies")

# Download model (~3 minutes)
!HF_XET_HIGH_PERFORMANCE=1 hf download microsoft/VibeVoice-1.5B --quiet  --local-dir /content/models/VibeVoice-1.5B > /dev/null
!HF_XET_HIGH_PERFORMANCE=1 hf download microsoft/VibeVoice-Large --quiet  --local-dir /content/models/VibeVoice-Large > /dev/null

print("✅ Downloaded model: microsoft/VibeVoice-1.5B")
print("✅ Downloaded model: microsoft/VibeVoice-Large")



    ⚠️ WARNING: T4 GPU not detected

    The recommended runtime for this Colab notebook is "T4 GPU".

    To change the runtime type:

        1. Click on "Runtime" in the top navigation menu
        2. Click on "Change runtime type"
        3. Select "T4 GPU"
        4. Click "OK" if a "Disconnect and delete runtime" window appears
        5. Click on "Save"

    
✅ Cloned VibeVoice repository
✅ Installed dependencies
✅ Downloaded model: microsoft/VibeVoice-1.5B
✅ Downloaded model: microsoft/VibeVoice-Large


In [5]:
!pip install -q flash-attn --no-build-isolation


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 128.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for flash-attn: filename=flash_attn-2.8.3-cp312-cp312-linux_x86_64.whl size=256040057 sha256=f25da18657a87fc83dc1bfb8b7751b82246e9db355510226b674fd437c34b5fb
  Stored in directory: /root/.cache/pip/wheels/3d/59/46/f282c12c73dd4bb3c2e3fe199f1a0d0f8cec06df0cccfeee27
Successfully built flash-attn


## Step 2: Create Transcript

In [2]:
%%writefile /content/my_transcript.txt
Speaker 1: Can I try VibeVoice with my own example? 你会说中文吗？
Speaker 2: 我会说中文. Of course! VibeVoice is open-source, built to benefit everyone - you're welcome to try it out.


Writing /content/my_transcript.txt


In [9]:
%%writefile /content/long-cat.txt
Speaker 1: 欢迎收听AI Radio FM - 科技频道，您的专属生成式AI播客！今天，我们聚焦一个非常引人注目的技术报告——美团LongCat团队的LongCat-Flash。weedge，这款拥有5600亿参数的MoE语言模型，据说是为计算效率和高级代理能力而生，听起来就让人兴奋，对吧？
speaker 2: 是的，我非常激动能聊聊这个！LongCat-Flash，哎呀，它简直就是将大模型的规模化效率和智能前沿推向了一个新高度。它不仅参数庞大，更重要的是它在架构和训练策略上，带来了很多颠覆性的创新，让人耳目一新。
Speaker 1: 嗯，听起来确实很厉害。5600亿参数，这个数字本身就足够惊人。但更吸引我的是它如何实现所谓的“计算效率”和“代理能力”。weedge，你能先给我们一个高屋建瓴的概览吗？是什么让LongCat-Flash在这两方面如此突出？
speaker 2: 当然！概括来说，LongCat-Flash的核心创新在于两大架构设计。第一是“零计算专家”机制，这让模型能够根据上下文需求动态地分配计算预算。你知道，并非所有token都同等重要，它平均每个token激活大约270亿参数，但实际会在186亿到313亿之间浮动，这大大优化了资源利用。第二是“快捷连接MoE”，也就是ScMoE，它巧妙地扩大了计算与通信的重叠窗口，显著提升了推理效率和吞吐量。
Speaker 1: 动态分配计算预算，快捷连接MoE，这些听起来都直指效率的核心。那么，这些创新最终转化成了怎样的实际性能指标呢？有没有一些数据能让我们直观感受到LongCat-Flash的强大？
speaker 2: 绝对有！这些架构上的突破，加上基础设施的协同优化，让LongCat-Flash的训练效率达到了惊人的水平。它在短短30天内，完成了超过20万亿tokens的预训练！想象一下，那是一个多么庞大的数据量。而在推理端，它在H800上实现了每秒超过100个tokens的输出速度，而且每百万输出token的成本仅为0.7美元。这效率，这成本控制，简直是业界的一个新标杆。
Speaker 1: 20万亿tokens在30天内完成训练，这速度，哇，太令人印象深刻了！而且推理成本也极具竞争力。除了效率，报告中还强调了LongCat-Flash的“代理能力”，这又该如何理解呢？它和其他大模型在代理任务上有什么不同？
speaker 2: 代理能力是LongCat-Flash的另一个杀手锏。为了培养这种能力，美团团队采取了一个多阶段的训练策略。首先是大规模预训练，然后是针对性的中后期训练，特别加强了推理、代码和指令遵循能力，还加入了合成数据和工具使用任务。这意味着它不仅仅是一个擅长聊天的模型，更是一个能够理解复杂指令、自主规划、与环境交互并利用工具来解决真实世界问题的“智能代理”。它在ArenaHard-V2、TerminalBench和τ2-Bench等代理任务基准上，都展现出了非凡的实力。
Speaker 1: 也就是说，LongCat-Flash不仅跑得快，而且还更聪明，更会解决问题。我们来深入探讨一下它的架构细节，特别是你提到的“零计算专家”。weedge，这个概念很有趣，它具体是如何实现动态计算的？又是如何保证负载均衡的呢？
speaker 2: 好的，零计算专家是MoE架构的一个精妙扩展。它的核心思想是，除了常规的FFN专家，我们还引入了'零计算专家'，这些专家不进行任何实际计算，只是简单地返回输入。这样，路由器就可以根据token的上下文重要性，动态选择激活不同数量的FFN专家和零计算专家。对于简单的token，它可能激活更多的零计算专家，从而节省计算资源；对于复杂的token，它会激活更多FFN专家，投入更多算力。这就像一个智能的资源调度系统，按需分配。为了确保负载均衡，我们采用了一个由PID控制器调节的专家偏差机制，它会动态调整路由分数，确保FFN专家平均被激活的数量保持在一个目标值，例如我们平均每个token激活了大约270亿参数，这其中FFN专家平均贡献了8个。这在训练过程中被严格跟踪，并有效降低了模型的验证损失。
Speaker 1: 我明白了，它通过引入‘什么都不做’的专家，实现了更精细的资源调度，真是个聪明的点子！那另一个关键架构‘快捷连接MoE’，或者叫ScMoE，又是如何解决MoE模型中通信瓶颈这个老大难问题的？
speaker 2: ScMoE的设计是为了解决大规模MoE模型中专家并行带来的通信开销问题。传统的MoE模型，在发送token给专家（dispatch）和接收结果（combine）时，通信和计算是顺序发生的，通信延迟会成为瓶颈。ScMoE通过引入一个跨层快捷连接，将前一个模块的FFN计算与当前MoE层的dispatch和combine通信并行执行。这意味着它大大扩展了计算-通信重叠的窗口。举个例子，就像是你在开车的时候，副驾可以同时帮你处理一些事情，而不是等你完全停下车再开始。这个创新在不牺牲模型质量的前提下，显著提升了训练和推理的效率，我们的实验也证实了，这种重新排序的执行方式，对模型性能几乎没有负面影响，训练损失曲线几乎与基线模型保持一致。
Speaker 1: 嗯，我懂了，通过巧妙的并行化，将通信隐藏在计算之后，从而提升了整体效率。除了这些核心的MoE结构创新，LongCat-Flash在架构设计上还有没有其他为了可扩展性而做的重要调整呢？比如，有没有一些细节是确保模型在从小规模到超大规模扩展时依然稳定和高性能的？
speaker 2: 当然有！我们非常重视可扩展性，并为此引入了“方差对齐设计”。这包括对Multi-head Latent Attention，也就是MLA机制的尺度校正，通过引入特定的缩放因子，解决了非对称低秩分解中固有的方差不平衡问题，确保模型在初始化时，查询和键向量的方差能够对齐，从而在模型扩展时保持更稳定的性能。另外，对于细粒度专家初始化，我们也设计了方差补偿机制，通过一个缩放因子来抵消专家分割导致的初始化方差降低。这些细节确保了模型在不断扩大规模时，其内部信号能够保持健康和稳定，避免了性能退化。这就像，嗯，确保一个大型管弦乐队在增加乐器和乐手时，每个部分的音量和音调都能完美协调一样。
Speaker 1: 这些都是非常底层的、但又极其关键的工程细节，确保了模型在规模化上的稳健性。weedge，训练这样一款5600亿参数的模型，并用20万亿tokens进行训练，这绝对是一个巨大的工程。团队是如何保证训练过程的稳定性和效率的？有没有一些独特的训练策略值得分享？
speaker 2: 是的，大规模训练的稳定性是一个巨大的挑战。我们采取了一整套全面的策略。首先是“超参数迁移”，我们先在一个较小的代理模型上找到最优超参数，然后通过理论验证的缩放规则，将这些超参数迁移到LongCat-Flash这样的超大模型上，这大大节省了寻找最优配置的成本和时间。其次是“模型增长初始化”，我们从一个预训练好的半尺度模型开始，通过层堆叠技术来扩展参数，这比随机初始化能带来更快的收敛和更好的性能。在实际训练中，这种策略在一开始可能会让损失略微上升，但随后会加速收敛并超越基线模型。
Speaker 1: 超参数迁移和模型增长初始化，这两个策略听起来都是为了更高效、更稳定地启动大规模训练。但即使如此，训练过程中难免会遇到各种不稳定的问题，比如梯度爆炸、激活值异常等等。LongCat-Flash是如何克服这些训练挑战的呢？
speaker 2: 这是我们投入了大量精力的地方！我们从三个维度增强了训练稳定性：首先是“路由器稳定性”，我们通过监控路由器权重相似度和梯度范数比，确保负载均衡损失不会过度主导语言模型损失，避免专家路由趋于同质化。其次是“激活稳定性”，我们引入了‘隐藏z-loss’，这是一个很小的损失项，但能有效抑制大规模激活的发生，防止训练过程中出现损失尖峰，这对于使用BF16混合精度训练尤其重要。最后，对于Adam优化器，我们发现它的epsilon参数在模型规模变大时变得非常关键，我们将其设置为1e-16，远小于通常的默认值，以确保优化器在面对小梯度时依然能保持自适应性。这些精细的调整，共同保障了LongCat-Flash在超大规模训练中的稳健性，让它在20万亿tokens的训练中，能够持续稳定地学习。
Speaker 1: 哇，听起来每一个环节都考虑得非常周全。weedge，听起来LongCat-Flash在效率和智能上都非常出色。但我有点好奇，对于这种大规模的MoE模型，它在训练和部署过程中，有没有遇到过一些特别棘手的平衡问题？比如，提升效率的同时，模型质量是否真的能完全保持，或者在某些方面需要做一些妥协？毕竟，鱼和熊掌兼得总是很难的，对吧？
speaker 2: 嗯，这是一个非常好的问题，也确实是我们在整个研发过程中不断思考和攻克的难点。你说得没错，追求效率和质量的平衡，这本身就是一场复杂的博弈。不过，LongCat-Flash的设计哲学就是尽可能地在不牺牲模型质量的前提下，最大化效率。例如，我们提到的Shortcut-connected MoE，通过架构上的创新，我们实证了它的引入几乎不影响模型的训练损失曲线，也就是说，它在提高吞吐量和降低延迟的同时，模型的学习能力和最终性能并没有受到负面影响。这在图4的训练损失曲线对比中得到了清晰的验证。又比如，零计算专家机制，它动态地分配计算预算，让模型能够将更多资源投入到真正‘难’的token上，这反而是一种更智能的资源利用方式，某种程度上是提升了质量。当然，在一些特定的优化点上，比如量化，我们确实需要在精度和速度之间寻找一个最优的平衡点，但这都是通过精细的层级混合精度量化策略来解决的，确保最终效果在可接受范围内。所以，可以自信地说，LongCat-Flash在这两方面找到了一个非常出色的协同点。
Speaker 1: 我明白了，并非是简单的取舍，而是通过更智能的设计和精细的平衡，实现了协同增效。LongCat-Flash在预训练阶段就非常强调数据质量和多样性，特别是为了代理能力，它还进行了推理和编码能力的增强。那么，针对Agentic Tool Use这种需要与环境交互的复杂任务，它的后训练是如何进行的？数据从何而来？
speaker 2: 这正是我们构建LongCat-Flash代理能力的关键。我们设计了一个多智能体数据合成框架，专门用于生成高质量、高挑战性的代理任务。这个框架聚焦于三个维度来提升任务难度：信息处理复杂性、工具集复杂性和用户交互复杂性。例如，我们有UserProfileAgent生成具有不同会话风格、沟通意愿和信息披露模式的用户，模拟真实用户；ToolSetAgent则通过随机漫步从庞大的工具图中采样子图，控制工具集的复杂性；InstructionAgent和EnvironmentAgent则负责生成复杂的任务指令和环境信息。通过这种方式，我们能够系统性地创建大量需要迭代推理和环境交互的复杂任务，并进行严格的质量筛选和响应选择，构建出冷启动训练集，确保模型能学习到真实的代理行为。
Speaker 1: 这听起来像是在模拟一个微缩的真实世界，通过多智能体协作来生成训练数据，真是太有创意了！这种方法能有效解决高质量代理任务数据稀缺的问题。除了模型架构和训练策略，支撑LongCat-Flash高效运行的基础设施也至关重要。weedge，在训练和推理的基础设施层面，团队又有哪些值得分享的突破？
speaker 2: 基础设施是看不见的英雄。我们首先在“数值精度控制和故障检测”上下了大功夫。通过ULP评估来量化浮点错误，并引入在线的“静默数据损坏（SDC）检测机制”，在空闲计算阶段重计算敏感操作，确保训练过程的数值正确性。其次是“核函数优化”，为了确保训练的确定性和可复现性，我们重新设计了FlashAttention Gradients等多个核函数，在保持确定性的同时，性能也能接近非确定性版本。比如，我们的确定性FAG核函数比原始确定性版本快1.6倍，只比非确定性版本慢5%。这些优化在保证计算正确性的同时，也大大提升了训练效率。
Speaker 1: 精度、确定性和性能，这三者在超大规模训练中缺一不可，听起来LongCat-Flash在这方面做得非常扎实。那么，在分布式训练策略上，比如如何高效地利用数万个加速器，美团团队又有哪些独到的见解和实现？
speaker 2: 在分布式策略上，我们采用了专家并行组（EP），每个组32个加速器。为了减少通信开销，注意力层采用上下文并行而非张量并行，FFN层则使用EP分区。关键在于，LongCat-Flash的ScMoE架构允许我们在单个批次内就实现dispatch和combine通信与计算的重叠。我们甚至将MoE层拆分成两个块，使其能与稠密FFN计算及自身进行重叠。此外，我们优化了all-gather/reduce-scatter通信核函数，并采用了V-ZB算法来平衡管道并行阶段的内存使用，将峰值内存降至60GB以下，实现了理论上的零气泡。这些都极大地提升了大规模训练的吞吐量和可用性，达到了98.48%的时间可用率，所有故障都能自动处理。
Speaker 1: 零气泡的管道并行，98.48%的可用率，这些数字再次印证了其在工程实现上的卓越。在推理和部署方面，LongCat-Flash如何将这种效率优势转化为实际的用户体验呢？比如，它达到了每秒100个tokens的推理速度，这背后有哪些模型特定和系统层面的优化？
speaker 2: 嗯，推理效率是决定用户体验的关键。在模型特定优化上，我们首先利用ScMoE结构实现了SBO，也就是“单批次重叠”调度策略。它将模块级的计算与通信深度并行，如图9所示，使得关键的all-to-all通信开销被隐藏起来。其次是“推测解码”，我们利用多token预测MTP作为草稿模型，它的接受率超过90%，大大加速了生成过程。MTP头我们甚至优化到了使用单层稠密网络，在保证高接受率的同时，最大限度地降低了草稿模型的开销。再者，MLA机制的KV缓存压缩，也显著减少了显存占用和带宽压力。
Speaker 1: SBO调度，结合MTP和KV缓存优化，听起来确实是环环相扣，将模型架构的优势发挥到了极致。那么，在系统层面，为了实现那种极致的低延迟和高吞吐，又有哪些通用性的推理技术被应用呢？
speaker 2: 系统层面，我们主要做了三件事。第一是“最小化调度开销”。我们采用了TVD融合策略，将目标模型前向、验证和草稿模型前向融合为一个CUDA图，避免了多次核函数启动的开销。更进一步，我们引入了“多步重叠调度器”，在一个调度迭代中启动多个前向步骤的核函数，彻底隐藏了CPU的调度和同步延迟，确保GPU持续高占用率。第二是“定制化核函数”。我们对MoE GEMM、通信核函数等进行了深度优化，例如MoE GEMM利用SwapAB技术，充分挖掘了Tensor Core的潜力；通信核函数则利用NVLink Sharp的硬件加速功能，实现了高效的数据传输。第三是“量化”。我们采用了细粒度的逐块量化和层级混合精度量化方案，确保在性能和精度之间找到最佳平衡，特别对一些敏感层进行了更精确的FP8量化。这些系统级的魔术，才真正将LongCat-Flash的推理性能推向了巅峰，实现了每秒100 tokens的惊人速度。
Speaker 1: 这真的是一个全栈的优化过程，从模型到系统，每一个环节都精雕细琢。那么，我们再回到那个令人兴奋的数字：每百万输出token成本0.7美元。这对于实际的Agent应用意味着什么？
speaker 2: 这意义非凡！对于基于ReACT模式的Agent应用，完成一个任务需要多轮模型交互，交互延迟直接影响用户体验。0.7美元的成本，加上H800上高达100 tokens/s的动作指令生成速度，意味着单轮工具调用延迟可以控制在1秒以内。这极大地提升了Agent应用的交互性，用户几乎感受不到模型的思考和工具调用的停顿，从而带来更流畅、更自然的体验。同时，这也为大规模部署和商业化应用提供了极大的成本优势。
Speaker 1: 非常棒的分析，这让这些技术指标变得更具象化，让我们看到了它在实际应用中的巨大潜力。最后，weedge，总结一下，LongCat-Flash这款模型的发布，你认为它对整个大语言模型领域，尤其是MoE架构和Agentic AI的发展，会带来怎样的影响？
speaker 2: LongCat-Flash的发布，我觉得是对整个大模型社区的一个重大贡献。它不仅展示了5600亿参数MoE模型在效率和代理能力上可以实现的突破，更关键的是，它为我们提供了一套行之有效的、可复现的解决方案。从零计算专家、ScMoE这样的架构创新，到超参数迁移、模型增长、多重训练稳定性保障，再到多智能体数据合成框架，以及端到端的推理优化，它在每个环节都给出了非常具体且高效的答案。最重要的是，美团团队将LongCat-Flash进行了开源。这意味着社区可以基于这些前沿成果进行更深入的研究，推动MoE架构、高质量数据策略和代理模型发展，无疑会加速整个AI领域的创新步伐。
Speaker 1: 开源！这确实是一个激动人心的消息，将这些宝贵的经验和技术贡献给社区，必将激发更多的创新。感谢weedge今天的精彩分享，为我们深入解读了LongCat-Flash这款突破性的模型。
speaker 2: 非常荣幸能来到这里，也很高兴能与听众分享这些内容，期待下次再有机会与大家探讨！
Speaker 1: 感谢您订阅AI Radio FM - 科技频道，我们下期再见！
speaker 2: 再见！

Overwriting /content/long-cat.txt


## Step 3: Generate Audio

In [ ]:
# Run Python script to generate audio from transcript
!python /content/VibeVoice/demo/inference_from_file.py \
    --model_path /content/models/VibeVoice-Large \
    --txt_path /content/my_transcript.txt \
    --speaker_names Bowen Xinran

# Display audio controls
from IPython.display import Audio
Audio("/content/outputs/my_transcript_generated.wav")


In [ ]:
# Run Python script to generate audio from transcript
!python /content/VibeVoice/demo/inference_from_file.py \
    --model_path /content/models/VibeVoice-Large \
    --txt_path /content/long-cat.txt \
    --speaker_names Bowen Xinran



In [ ]:
# Display audio controls
from IPython.display import Audio
Audio("/content/outputs/long-cat_generated.wav")


In [ ]:
# Install ffmpeg
!apt-get update && apt-get install ffmpeg -y -qq


In [16]:
# Convert WAV to MP3
!ffmpeg -i /content/outputs/long-cat_generated.wav /content/outputs/long-cat_generated.mp3


ffmpeg version 4.4.2-0ubuntu0.22.04.1 Copyright (c) 2000-2021 the FFmpeg developers
  built with gcc 11 (Ubuntu 11.2.0-19ubuntu1)
  configuration: --prefix=/usr --extra-version=0ubuntu0.22.04.1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enab

In [17]:
!ls -lh /content/outputs/*

-rw-r--r-- 1 root root 3.7M Sep  1 11:51 /content/outputs/long-cat_generated.mp3
-rw-r--r-- 1 root root  44M Sep  1 11:18 /content/outputs/long-cat_generated.wav
-rw-r--r-- 1 root root 582K Sep  1 10:43 /content/outputs/my_transcript_generated.wav


In [18]:
# Display audio controls for the new MP3 file
from IPython.display import Audio
Audio("/content/outputs/long-cat_generated.mp3")

# upload audio

In [ ]:
!pip install -q boto3

In [22]:
from google.colab import userdata
CLOUDFLARE_ACCOUNT_ID=userdata.get('CLOUDFLARE_ACCOUNT_ID')
CLOUDFLARE_ACCESS_KEY=userdata.get('CLOUDFLARE_ACCESS_KEY')
CLOUDFLARE_SECRET_KEY=userdata.get('CLOUDFLARE_SECRET_KEY')
CLOUDFLARE_REGION=userdata.get('CLOUDFLARE_REGION')
S3_BUCKET_URL=userdata.get('S3_BUCKET_URL')




In [23]:
import os
import logging

from tqdm import tqdm
import boto3


def r2_upload(remote_folder: str, local_file: str) -> str:
    account_id = CLOUDFLARE_ACCOUNT_ID
    access_key = CLOUDFLARE_ACCESS_KEY
    secret_key = CLOUDFLARE_SECRET_KEY
    region_name = CLOUDFLARE_REGION
    endpoint_url = f"https://{account_id}.r2.cloudflarestorage.com"
    return upload(remote_folder, local_file, endpoint_url, access_key, secret_key, region_name)

def upload(
    remote_folder: str,
    local_file: str,
    endpoint_url: str = "",
    access_key: str = "",
    secret_key: str = "",
    region_name: str = "",
) -> str:
    endpoint_url = endpoint_url or os.getenv("AWS_ENDPOINT_URL")
    access_key = access_key or os.getenv("AWS_ACCESS_KEY")
    secret_key = secret_key or os.getenv("AWS_SECRET_KEY")
    region_name = region_name or os.getenv("AWS_REGION")
    s3 = boto3.client(
        service_name="s3",
        endpoint_url=endpoint_url,
        aws_access_key_id=access_key,
        aws_secret_access_key=secret_key,
        region_name=region_name,  # Must be one of: wnam, enam, weur, eeur, apac, auto
    )
    file_name = os.path.basename(local_file)
    file_size = os.path.getsize(local_file)
    print(f"Name: {file_name} Size: {round(file_size/1024,2)} KB")

    with tqdm(
        total=file_size, unit="B", unit_scale=True, desc=f"Uploading {file_name} to R2", ascii=True
    ) as pbar:
        with open(local_file, "rb") as f:
            s3.upload_fileobj(f, remote_folder, file_name, Callback=lambda x: pbar.update(x))
    object_information = s3.head_object(Bucket=remote_folder, Key=file_name)
    print(f"Upload {local_file} ok,object_information: {object_information}")

    # Delete object
    # s3.delete_object(Bucket=remote_folder, Key=file_name)
    return get_url(file_name)

def get_url(file_name: str):
    bucket_url = S3_BUCKET_URL
    url = f"{bucket_url}/{file_name}"
    print(f"url:{url}")

    return url

In [24]:
r2_upload("podcast", "/content/outputs/long-cat_generated.mp3")

Name: long-cat_generated.mp3 Size: 3707.76 KB


Uploading long-cat_generated.mp3 to R2: 100%|##########| 3.80M/3.80M [00:01<00:00, 2.01MB/s]

Upload /content/outputs/long-cat_generated.mp3 ok,object_information: {'ResponseMetadata': {'HTTPStatusCode': 200, 'HTTPHeaders': {'date': 'Mon, 01 Sep 2025 12:02:26 GMT', 'content-type': 'audio/mpeg', 'content-length': '3796749', 'connection': 'keep-alive', 'accept-ranges': 'bytes', 'etag': '"b1b72710daa9d0e0a0016e6b1eb85001"', 'last-modified': 'Mon, 01 Sep 2025 12:02:26 GMT', 'vary': 'Accept-Encoding', 'server': 'cloudflare', 'cf-ray': '97849e645bfbff83-SIN'}, 'RetryAttempts': 0}, 'AcceptRanges': 'bytes', 'LastModified': datetime.datetime(2025, 9, 1, 12, 2, 26, tzinfo=tzutc()), 'ContentLength': 3796749, 'ETag': '"b1b72710daa9d0e0a0016e6b1eb85001"', 'ContentType': 'audio/mpeg', 'Metadata': {}}
url:https://pub-f8da0a7ab3e74cc8a8081b2d4b8be851.r2.dev/long-cat_generated.mp3


'https://pub-f8da0a7ab3e74cc8a8081b2d4b8be851.r2.dev/long-cat_generated.mp3'